# Lyrics Analysis

In [226]:
lyrics_directory = "Lyrics_Data/"
tracks_csv = "tracks_group.csv"
stopwords_file = "stopwords.txt"

In [227]:
target_group = "kpop"
kpop_group = set(['kpop', 'itzy', 'seventeen', 'bts', 'twice'])
global_group = set(['global', 'billboard'])

target_and_kpop = kpop_group.union(set([target_group]))
target_and_global = global_group.union(set([target_group]))

## Import data

In [228]:
import pandas as pd

In [229]:
df = pd.read_csv(tracks_csv)

df.head(3)

track_name                track_id grouping
0  Ice Cream (with Selena Gomez)  2J4P46vCFm1rPkNkp9pZWX     kpop
1                       Dynamite  0v1x6rN6JHRapa03JElljE     kpop
2                    THE BADDEST  2V4Fx72svQRxrFvNT1eq5f     kpop

In [230]:
#all to "kpop"
df.loc[df['grouping'].isin(target_and_kpop), 'grouping'] = "kpop"

In [231]:
df.shape

(4618, 3)

In [232]:
df["grouping"].unique()

array(['kpop', 'global', 'billboard'], dtype=object)

In [233]:
def get_lyrics(track_id):
    try:
        lyrics = ""
        with open(lyrics_directory + track_id + ".txt", "r") as f:
            lyrics = f.read()
            
        return lyrics            
    except:
        return None
    
df["lyrics"] = df["track_id"].apply(get_lyrics)

df.shape

(4618, 4)

In [234]:
# stop words
# https://www.kaggle.com/datasets/rowhitswami/stopwords/
stopwords = set()
with open(stopwords_file, "r") as f:
    stopwords = set(f.read().split("\n"))
    
stopwords

{',',
 '>',
 '?',
 'Just',
 'Yes',
 'a',
 'abaft',
 'abafter',
 'abaftest',
 'about',
 'abouter',
 'aboutest',
 'above',
 'abover',
 'abovest',
 'accordingly',
 'aer',
 'aest',
 'afore',
 'after',
 'afterer',
 'afterest',
 'afterward',
 'afterwards',
 'again',
 'against',
 'aid',
 'ain',
 'albeit',
 'all',
 'aller',
 'allest',
 'alls',
 'allyou',
 'almost',
 'along',
 'alongside',
 'already',
 'also',
 'although',
 'always',
 'amid',
 'amidst',
 'among',
 'amongst',
 'an',
 'and',
 'andor',
 'anear',
 'anent',
 'another',
 'any',
 'anybody',
 'anyhow',
 'anyone',
 'anything',
 'anywhere',
 'apart',
 'aparter',
 'apartest',
 'appear',
 'appeared',
 'appearing',
 'appears',
 'appropriate',
 'appropriated',
 'appropriater',
 'appropriates',
 'appropriatest',
 'appropriating',
 'are',
 'ares',
 'around',
 'as',
 'ases',
 'aside',
 'asides',
 'aslant',
 'astraddle',
 'astraddler',
 'astraddlest',
 'astride',
 'astrider',
 'astridest',
 'at',
 'athwart',
 'atop',
 'atween',
 'aught',
 'aught

## Analyze

In [235]:
def is_stopword(word):
    word = word.lower()
    
    if len(word) <= 1:
        return True
    
    # in the list
    if word in stopwords:
        return True
    
    # is Korean
    if ord("가") <= ord(word[0]) <= ord("힣"):
        return True
    
    return False

### Characteristic Keyword
Using TF-IDF

In [236]:
from sklearn.feature_extraction.text import TfidfVectorizer

#### Among global

In [237]:
df_looking = df[df["grouping"].isin(target_and_global)].reset_index(drop=True)

In [238]:
vectorizer = TfidfVectorizer(stop_words=list(stopwords), max_features=1000, min_df=10)

x = vectorizer.fit_transform(df_looking["lyrics"].fillna("")).toarray()

df_tfidf = pd.DataFrame(x, columns=vectorizer.get_feature_names_out()).T

c:\Users\Hiyoko\.conda\envs\data\lib\site-packages\sklearn\feature_extraction\text.py:408: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['vis', 'viser', 'visest', 'yes'] not in stop_words.
  warnings.warn(


In [239]:
threshold = 0.001
counter = {}
summer = {}

for cnt in range(len(df_looking)):
    if df_looking["grouping"][cnt] != target_group:
        continue
    
    tfidf_series = df_tfidf[cnt]
    
    keywords = tfidf_series[tfidf_series > threshold].index.tolist()
    for keyword in keywords:
        counter[keyword] = counter.get(keyword, 0) + 1
        summer[keyword] = summer.get(keyword, 0) + tfidf_series[keyword]

In [240]:
def sort_dictionary(dictionary):
    return [(k, dictionary[k]) for k in sorted(dictionary, key=dictionary.get, reverse=True)]

In [241]:
tfidf_counter_global = sort_dictionary(counter)
tfidf_counter_global

[('love', 521),
 ('let', 507),
 ('sorry', 497),
 ('news', 412),
 ('home', 410),
 ('heart', 362),
 ('yes', 345),
 ('eyes', 313),
 ('baby', 311),
 ('feel', 301),
 ('say', 299),
 ('think', 292),
 ('back', 279),
 ('night', 270),
 ('take', 267),
 ('world', 239),
 ('new', 226),
 ('follow', 224),
 ('only', 220),
 ('am', 217),
 ('need', 212),
 ('tell', 206),
 ('life', 202),
 ('leave', 202),
 ('light', 199),
 ('dream', 199),
 ('keep', 195),
 ('room', 190),
 ('give', 179),
 ('way', 177),
 ('end', 171),
 ('mind', 170),
 ('down', 162),
 ('wait', 149),
 ('still', 146),
 ('hands', 143),
 ('child', 142),
 ('show', 140),
 ('dance', 139),
 ('girl', 139),
 ('looking', 136),
 ('care', 135),
 ('price_varies', 133),
 ('contact', 133),
 ('little', 130),
 ('hear', 128),
 ('ah', 128),
 ('okay', 126),
 ('away', 125),
 ('honey', 122),
 ('boy', 121),
 ('beautiful', 121),
 ('sleep', 119),
 ('find', 119),
 ('start', 119),
 ('ready', 118),
 ('feeling', 118),
 ('bad', 117),
 ('stay', 116),
 ('call', 115),
 ('sky', 1

In [242]:
tfidf_summer_global = sort_dictionary(summer)
tfidf_summer_global

[('love', 90.37153562331105),
 ('home', 76.21004040264718),
 ('sorry', 69.1397655218261),
 ('news', 48.08603122812252),
 ('let', 45.65971006638431),
 ('heart', 43.53378986841094),
 ('yes', 39.32657988099398),
 ('baby', 37.152868190550656),
 ('한국', 32.36819854379235),
 ('follow', 32.046654207752745),
 ('eyes', 30.337788713241792),
 ('night', 30.09200698624242),
 ('feel', 28.39620085138629),
 ('dream', 27.485997323149512),
 ('back', 27.444226966689936),
 ('world', 27.138972303382236),
 ('new', 25.668929887759134),
 ('say', 25.19307183864961),
 ('ah', 24.989323963741565),
 ('light', 24.884317238554694),
 ('only', 24.528770918077953),
 ('think', 24.049286804765085),
 ('woo', 23.311984021567397),
 ('room', 22.957403813727545),
 ('am', 22.89032814755495),
 ('dance', 22.81597776759301),
 ('need', 22.554843859626192),
 ('life', 21.359150404595603),
 ('contact', 20.8388989921961),
 ('hot', 20.835045446552304),
 ('give', 20.800300456215705),
 ('boy', 20.55275934228878),
 ('end', 19.7053305786462

#### Among KPOP

In [243]:
df_looking = df[df["grouping"].isin(target_and_kpop)].reset_index(drop=True)

In [244]:
vectorizer = TfidfVectorizer(stop_words=list(stopwords), max_features=1000, min_df=10)

x = vectorizer.fit_transform(df_looking["lyrics"].fillna("")).toarray()

df_tfidf = pd.DataFrame(x, columns=vectorizer.get_feature_names_out()).T

c:\Users\Hiyoko\.conda\envs\data\lib\site-packages\sklearn\feature_extraction\text.py:408: UserWarning: Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['vis', 'viser', 'visest', 'yes'] not in stop_words.
  warnings.warn(


In [245]:
threshold = 0.001
counter = {}
summer = {}

for cnt in range(len(df_looking)):
    if df_looking["grouping"][cnt] != target_group:
        continue
    
    tfidf_series = df_tfidf[cnt]
    
    keywords = tfidf_series[tfidf_series > threshold].index.tolist()
    for keyword in keywords:
        counter[keyword] = counter.get(keyword, 0) + 1
        summer[keyword] = summer.get(keyword, 0) + tfidf_series[keyword]

In [246]:
tfidf_counter_kpop = sort_dictionary(counter)
tfidf_counter_kpop

[('love', 521),
 ('let', 507),
 ('sorry', 497),
 ('news', 413),
 ('home', 408),
 ('heart', 363),
 ('yes', 345),
 ('eyes', 313),
 ('baby', 312),
 ('feel', 301),
 ('say', 299),
 ('think', 292),
 ('back', 279),
 ('night', 271),
 ('take', 267),
 ('world', 239),
 ('new', 226),
 ('follow', 224),
 ('only', 221),
 ('am', 217),
 ('need', 212),
 ('tell', 207),
 ('life', 202),
 ('leave', 202),
 ('light', 199),
 ('dream', 199),
 ('keep', 195),
 ('room', 190),
 ('give', 179),
 ('way', 177),
 ('end', 171),
 ('mind', 170),
 ('down', 162),
 ('wait', 149),
 ('still', 146),
 ('hands', 144),
 ('child', 142),
 ('show', 140),
 ('dance', 139),
 ('girl', 139),
 ('looking', 136),
 ('care', 135),
 ('price_varies', 133),
 ('contact', 133),
 ('little', 130),
 ('hear', 128),
 ('ah', 128),
 ('away', 125),
 ('okay', 125),
 ('honey', 122),
 ('boy', 121),
 ('beautiful', 121),
 ('sleep', 119),
 ('find', 119),
 ('start', 119),
 ('feeling', 118),
 ('bad', 117),
 ('ready', 117),
 ('stay', 116),
 ('call', 115),
 ('sky', 1

In [247]:
tfidf_summer_kpop = sort_dictionary(summer)
tfidf_summer_kpop

[('love', 93.38607915430586),
 ('home', 67.60988950474074),
 ('sorry', 50.59637894638318),
 ('let', 47.93110110384121),
 ('heart', 41.116791964066365),
 ('yes', 41.10677536323856),
 ('baby', 38.186684222047816),
 ('news', 31.517989144550324),
 ('feel', 31.44896588575648),
 ('night', 31.329232070269644),
 ('say', 29.465943981617627),
 ('back', 28.917235907807306),
 ('only', 27.346261757010232),
 ('eyes', 27.17744214823235),
 ('think', 25.90023701555005),
 ('follow', 25.761256945043133),
 ('need', 25.761205628558344),
 ('world', 25.658269008485153),
 ('한국', 25.315827692846227),
 ('am', 24.95654988991367),
 ('take', 24.1156828940417),
 ('life', 23.881421538952736),
 ('give', 23.697773262598623),
 ('new', 23.122089100039577),
 ('ah', 22.84938734799792),
 ('dream', 22.769037842367304),
 ('light', 22.613825747417657),
 ('dance', 21.8695620276186),
 ('tell', 21.632868387047996),
 ('woo', 21.403899689771514),
 ('boy', 20.841865832124057),
 ('leave', 20.144998389279486),
 ('room', 19.6380575782

### Topic analysis

In [248]:
from gensim.corpora.dictionary import Dictionary
from gensim.models import LdaModel

In [249]:
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis
def save_lda_vis(lda, corpus, dictionary, filename):
    vis = gensimvis.prepare(lda, corpus, dictionary)
    pyLDAvis.save_html(vis, filename)
    
    with open(filename, "r") as f:
        html = f.read()
        
    return html, vis

In [250]:
def pre_process(df_lyrics):
    # tokenize lyrics
    lyrics_processed = df_lyrics.fillna("").str.split()

    for _list in lyrics_processed:
        for cnt in range(len(_list)):
            _list[cnt] = _list[cnt].replace(".", "").replace(",", "").replace("?", "").replace("\\", "").replace("/", "").replace(":", "").lower()
            
            if is_stopword(_list[cnt]):
                _list[cnt] = ""
                
    # remove empty string
    for cnt in range(len(lyrics_processed)):
        while(True):
            try:
                lyrics_processed[cnt].remove("")
            except:
                break

    return lyrics_processed

#### Among global

In [251]:
df_looking = df[df["grouping"].isin(target_and_global)].reset_index(drop=True)

In [252]:
#train model
lyrics_processed = pre_process(df_looking["lyrics"])
dictionary = Dictionary(lyrics_processed)
corpus = [dictionary.doc2bow(text) for text in lyrics_processed]
lda = LdaModel(corpus=corpus, id2word=dictionary, num_topics=100)

all topics

In [253]:
lda_html_global, vis = save_lda_vis(lda, corpus, dictionary, "lda.html")

vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
57    -0.136582  0.001762       1        1  4.250502
75    -0.147132  0.021352       2        1  3.950830
6     -0.073628 -0.036140       3        1  3.539659
40    -0.060303 -0.034940       4        1  3.263384
47    -0.077738 -0.027629       5        1  2.987383
...         ...       ...     ...      ...       ...
8      0.061781  0.000620      96        1  0.306681
78     0.101816 -0.056797      97        1  0.302119
71     0.117340 -0.008747      98        1  0.299776
50     0.134670 -0.037033      99        1  0.292994
46     0.154661 -0.062752     100        1  0.286200

[100 rows x 5 columns], topic_info=        Term         Freq        Total  Category  logprob  loglift
280    child  5676.000000  5676.000000   Default  30.0000  30.0000
7603  labour  4193.000000  4193.000000   Default  29.0000  29.0000
494     cake  2272.000000  2272.000000   Default  28.0000  28.0000
425    drunk  2643.000000  2643.000000   Default  27.0000  27.0000
120     home  4263.000000  4263.000000   Default  26.0000  26.0000
...      ...          ...          ...       ...      ...      ...
403     feel    10.706644  3476.699118  Topic100  -5.0406   0.0733
799      it!     8.355628   365.928814  Topic100  -5.2886   2.0767
489     work     9.551100  2363.765716  Topic100  -5.1548   0.3449
588     body     8.373698   863.941869  Topic100  -5.2864   1.2198
215    makes     8.220416   572.679447  Topic100  -5.3049   1.6125

[6112 rows x 6 columns], token_table=       Topic      Freq  Term
term                        
5816      12  0.043728  "all
5816      15  0.131185  "all
5816      18  0.612198  "all
5816      22  0.043728  "all
13290     23  0.946473   "be
...      ...       ...   ...
1418      61  0.765344    和지
3872      22  0.821330    和집
4415      94  0.966650    和하
2617      15  0.608102   日本語
2617      23  0.324321   日本語

[48024 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[58, 76, 7, 41, 48, 32, 63, 36, 88, 23, 40, 10, 60, 89, 77, 49, 94, 15, 14, 71, 55, 61, 74, 84, 22, 82, 99, 95, 87, 80, 1, 34, 29, 97, 83, 75, 27, 18, 33, 4, 56, 39, 68, 43, 50, 73, 81, 52, 78, 91, 90, 85, 96, 67, 13, 92, 57, 37, 5, 66, 54, 8, 98, 25, 45, 3, 62, 100, 24, 12, 42, 70, 6, 19, 59, 28, 46, 35, 30, 31, 86, 64, 38, 93, 17, 20, 21, 2, 16, 53, 44, 69, 65, 26, 11, 9, 79, 72, 51, 47])

what topics are in kpop?

In [254]:
threshold = 0.3

counter = {}
summer = {}

for cnt in range(len(df_looking)):
    if df_looking["grouping"][cnt] != target_group:
        continue
    
    topics = lda.get_document_topics(corpus[cnt], minimum_probability=0)
    
    for topic in topics:
        if topic[1] > threshold:
            counter[topic[0]] = counter.get(topic[0], 0) + 1
            
        summer[topic[0]] = summer.get(topic[0], 0) + topic[1]

In [255]:
_lda_counter_global = sort_dictionary(counter)
lda_counter_global = []
for tup in _lda_counter_global:
    new_tup = [tup[0], tup[1], lda.show_topic(tup[0])]
    lda_counter_global.append(new_tup)
    
lda_counter_global

[[87,
  85,
  [('news', 0.04289429),
   ('follow', 0.026165318),
   ('dream', 0.01991323),
   ('love', 0.019173887),
   ('sorry', 0.018631585),
   ('comment', 0.01464182),
   ('thank', 0.011577933),
   ('reply', 0.011338858),
   ('heart', 0.011100372),
   ('wind', 0.010576904)]],
 [75,
  80,
  [('love', 0.15492243),
   ("can't", 0.04945694),
   ('heart', 0.02459547),
   ('let', 0.018919557),
   ('say', 0.017806232),
   ('leave', 0.015767282),
   ('invalid', 0.01109536),
   ('am', 0.010856405),
   ('tell', 0.008671306),
   ('fall', 0.008320119)]],
 [57,
  66,
  [('night', 0.0368632),
   ('heart', 0.034493197),
   ('love', 0.01927269),
   ("can't", 0.011760459),
   ('feel', 0.010853962),
   ('last', 0.010673516),
   ('fall', 0.010566911),
   ('away', 0.010069458),
   ('place', 0.0074376655),
   ("there's", 0.0068359785)]],
 [22,
  54,
  [('sorry', 0.09309182),
   ('contact', 0.03268352),
   ('best', 0.02625319),
   ('ooh', 0.021783883),
   ('news', 0.01899677),
   ('life', 0.016826445),


In [256]:
_lda_summer_global = sort_dictionary(summer)
lda_summer_global = []
for tup in _lda_summer_global:
    new_tup = [tup[0], tup[1], lda.show_topic(tup[0])]
    lda_summer_global.append(new_tup)
    
lda_summer_global

[[87,
  88.13383587018916,
  [('news', 0.04289429),
   ('follow', 0.026165318),
   ('dream', 0.01991323),
   ('love', 0.019173887),
   ('sorry', 0.018631585),
   ('comment', 0.01464182),
   ('thank', 0.011577933),
   ('reply', 0.011338858),
   ('heart', 0.011100372),
   ('wind', 0.010576904)]],
 [22,
  73.67419282844048,
  [('sorry', 0.09309182),
   ('contact', 0.03268352),
   ('best', 0.02625319),
   ('ooh', 0.021783883),
   ('news', 0.01899677),
   ('life', 0.016826445),
   ('feel', 0.014067579),
   ('questions', 0.013022735),
   ('love', 0.012295544),
   ('think', 0.011384073)]],
 [75,
  73.18346166644506,
  [('love', 0.15492243),
   ("can't", 0.04945694),
   ('heart', 0.02459547),
   ('let', 0.018919557),
   ('say', 0.017806232),
   ('leave', 0.015767282),
   ('invalid', 0.01109536),
   ('am', 0.010856405),
   ('tell', 0.008671306),
   ('fall', 0.008320119)]],
 [57,
  59.28967273997432,
  [('night', 0.0368632),
   ('heart', 0.034493197),
   ('love', 0.01927269),
   ("can't", 0.0117

#### Among KPOP

In [257]:
df_looking = df[df["grouping"].isin(target_and_kpop)].reset_index(drop=True)

In [258]:
#train model
lyrics_processed = pre_process(df_looking["lyrics"])
dictionary = Dictionary(lyrics_processed)
corpus = [dictionary.doc2bow(text) for text in lyrics_processed]
lda = LdaModel(corpus=corpus, id2word=dictionary, num_topics=100)

# observe topics
topics = lda.print_topics()

In [259]:
threshold = 0.3

counter = {}
summer = {}

for cnt in range(len(df_looking)):
    if df_looking["grouping"][cnt] != target_group:
        continue
    
    topics = lda.get_document_topics(corpus[cnt], minimum_probability=0)
    
    for topic in topics:
        if topic[1] > threshold:
            counter[topic[0]] = counter.get(topic[0], 0) + 1
            
        summer[topic[0]] = summer.get(topic[0], 0) + topic[1]


In [260]:
lda_html_kpop, vis = save_lda_vis(lda, corpus, dictionary, "lda.html")

vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
26     0.377975  0.066954       1        1  3.658035
54     0.007285 -0.099628       2        1  2.551388
32     0.001121  0.025360       3        1  2.509367
50     0.016246 -0.058189       4        1  2.096816
69     0.012589  0.068006       5        1  2.009555
...         ...       ...     ...      ...       ...
23    -0.016432  0.002333      96        1  0.383081
91    -0.005487 -0.001358      97        1  0.370171
28    -0.003914  0.023424      98        1  0.368079
96     0.297683  0.021555      99        1  0.343588
12    -0.033722  0.072545     100        1  0.292186

[100 rows x 5 columns], topic_info=        Term         Freq        Total  Category  logprob  loglift
280    child  4282.000000  4282.000000   Default  30.0000  30.0000
425    drunk  2160.000000  2160.000000   Default  29.0000  29.0000
494     cake  1153.000000  1153.000000   Default  28.0000  28.0000
780  singing   728.000000   728.000000   Default  27.0000  27.0000
101    dance  1397.000000  1397.000000   Default  26.0000  26.0000
..       ...          ...          ...       ...      ...      ...
87        am     2.222730   501.678177  Topic100  -5.2434   0.4163
39     heart     2.151776   834.507601  Topic100  -5.2758  -0.1250
316     give     1.987955   447.908420  Topic100  -5.3550   0.4181
130     life     1.858799   458.933814  Topic100  -5.4222   0.3266
9      can't     1.888786   923.318834  Topic100  -5.4062  -0.3565

[6570 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
5866     16  0.089016       !!
5866     26  0.267048       !!
5866     49  0.445081       !!
5866     56  0.089016       !!
5867     26  0.849471  !evole!
...     ...       ...      ...
5606     43  0.489197       繁)
4295     44  0.586170       誰も
9717     89  0.388457     進むほど
8145     29  0.737334       道道
4296     44  0.586037       闇夜

[30197 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[27, 55, 33, 51, 70, 77, 42, 3, 7, 68, 88, 54, 63, 36, 43, 18, 59, 23, 65, 57, 6, 20, 39, 11, 93, 45, 96, 25, 49, 15, 32, 53, 34, 82, 86, 14, 87, 69, 72, 5, 62, 89, 66, 30, 22, 50, 95, 74, 40, 31, 91, 75, 19, 41, 16, 38, 26, 1, 35, 94, 79, 4, 37, 78, 44, 9, 98, 56, 83, 99, 76, 58, 21, 73, 60, 85, 81, 71, 47, 12, 100, 46, 61, 90, 48, 84, 17, 80, 52, 67, 28, 10, 2, 8, 64, 24, 92, 29, 97, 13])

In [261]:
_lda_counter_kpop = sort_dictionary(counter)
lda_counter_kpop = []
for tup in _lda_counter_kpop:
    new_tup = [tup[0], tup[1], lda.show_topic(tup[0])]
    lda_counter_kpop.append(new_tup)
    
lda_counter_kpop

[[54,
  42,
  [('invalid', 0.1606126),
   ('love', 0.12461457),
   ('let', 0.01243627),
   ('heart', 0.009340829),
   ('baby', 0.009229055),
   ("can't", 0.0086867),
   ('put', 0.008469698),
   ('crazy', 0.008280758),
   ('yes', 0.0073825563),
   ('red', 0.0056890612)]],
 [76,
  37,
  [('love', 0.15314466),
   ('poppy', 0.019765817),
   ('ay', 0.016668314),
   ('girl', 0.010858091),
   ('switch', 0.0086532235),
   ('cuz', 0.008572694),
   ('need', 0.008396274),
   ('night', 0.008323848),
   ('ya', 0.008206646),
   ('heart', 0.0070511904)]],
 [2,
  37,
  [('love', 0.04198856),
   ('last', 0.013476173),
   ('sorry', 0.011528366),
   ('home', 0.011520111),
   ("can't", 0.010993993),
   ('follow', 0.010836542),
   ('young', 0.010775717),
   ('news', 0.00832369),
   ('feel', 0.007825114),
   ('think', 0.0074157114)]],
 [41,
  30,
  [('love', 0.03762338),
   ('sorry', 0.025627404),
   ('flower', 0.024980024),
   ('call', 0.020167617),
   ('bum', 0.012719856),
   ("let's", 0.010112779),
   ('

In [262]:
_lda_summer_kpop = sort_dictionary(summer)
lda_summer_kpop = []
for tup in _lda_summer_kpop:
    new_tup = [tup[0], tup[1], lda.show_topic(tup[0])]
    lda_summer_kpop.append(new_tup)
    
lda_summer_kpop

[[54,
  40.85527960009631,
  [('invalid', 0.1606126),
   ('love', 0.12461457),
   ('let', 0.01243627),
   ('heart', 0.009340829),
   ('baby', 0.009229055),
   ("can't", 0.0086867),
   ('put', 0.008469698),
   ('crazy', 0.008280758),
   ('yes', 0.0073825563),
   ('red', 0.0056890612)]],
 [76,
  40.6421892360172,
  [('love', 0.15314466),
   ('poppy', 0.019765817),
   ('ay', 0.016668314),
   ('girl', 0.010858091),
   ('switch', 0.0086532235),
   ('cuz', 0.008572694),
   ('need', 0.008396274),
   ('night', 0.008323848),
   ('ya', 0.008206646),
   ('heart', 0.0070511904)]],
 [2,
  33.142739684027674,
  [('love', 0.04198856),
   ('last', 0.013476173),
   ('sorry', 0.011528366),
   ('home', 0.011520111),
   ("can't", 0.010993993),
   ('follow', 0.010836542),
   ('young', 0.010775717),
   ('news', 0.00832369),
   ('feel', 0.007825114),
   ('think', 0.0074157114)]],
 [41,
  31.945292953068474,
  [('love', 0.03762338),
   ('sorry', 0.025627404),
   ('flower', 0.024980024),
   ('call', 0.02016761

### Emotion analysis
Emotions:  
fear
anger
anticipation
trust
surprise
positive
negative
sadness
disgust
joy

In [263]:
import numpy as np

In [264]:
emotions = [
    "anger",
    "anticipation",
    "disgust",
    "fear",
    "joy",
    "negative",	
    "positive",
    "sadness",
    "surprise",	
    "trust",
]

In [265]:
df_nrc = pd.read_csv("NRC.txt", sep="\t", names=["word", "emotion", "amount"])

words_to_emotions = {}

for _, row in df_nrc.iterrows():
    words_to_emotions[row["word"]] = words_to_emotions.get(row["word"], np.zeros((10, 1)))
    words_to_emotions[row["word"]][emotions.index(row["emotion"])] = row["amount"]

In [266]:
df_emotion = df.copy()
for emotion in emotions:
    df_emotion[emotion] = 0

In [267]:
for cnt in range(len(df)):
    lyrics = df["lyrics"][cnt]

    if type(lyrics) != str:
        continue

    emotion_this = np.zeros((10, 1))

    for word in lyrics.split():
        if word in words_to_emotions:
            emotion_this += words_to_emotions[word]
            
    if np.linalg.norm(emotion_this) != 0:
        emotion_this /= np.linalg.norm(emotion_this)
        
    for emotion in emotions:
        df_emotion[emotion][cnt] = emotion_this[emotions.index(emotion)]

C:\Users\Hiyoko\AppData\Local\Temp\ipykernel_8924\3182639529.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_emotion[emotion][cnt] = emotion_this[emotions.index(emotion)]
C:\Users\Hiyoko\AppData\Local\Temp\ipykernel_8924\3182639529.py:17: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '[0.06561363]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  df_emotion[emotion][cnt] = emotion_this[emotions.index(emotion)]
C:\Users\Hiyoko\AppData\Local\Temp\ipykernel_8924\3182639529.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-

In [268]:
df_emotion_global = df_emotion[df_emotion["grouping"].isin(global_group)]
mean_emotion_global = df_emotion_global[emotions].mean()
normalized_mean_emotion_global = mean_emotion_global / np.linalg.norm(mean_emotion_global)

df_emotion_kpop = df_emotion[df_emotion["grouping"].isin(kpop_group)]
mean_emotion_kpop = df_emotion_kpop[emotions].mean()
normalized_mean_emotion_kpop = mean_emotion_kpop / np.linalg.norm(mean_emotion_kpop)

df_emotion_target = df_emotion[df_emotion["grouping"] == target_group]
mean_emotion_target = df_emotion_target[emotions].mean()
normalized_mean_emotion_target = mean_emotion_target / np.linalg.norm(mean_emotion_target)

In [269]:
normalized_mean_emotion_target

anger           0.157894
anticipation    0.321387
disgust         0.099041
fear            0.207745
joy             0.388888
negative        0.358769
positive        0.626679
sadness         0.217019
surprise        0.166724
trust           0.266915
dtype: float64

against global

In [270]:
emotion_percentage_global = (normalized_mean_emotion_target - normalized_mean_emotion_global) / normalized_mean_emotion_global * 100

emotion_percentage_global

anger          -25.268986
anticipation     8.704336
disgust        -27.502075
fear           -11.956912
joy             12.735731
negative       -22.729707
positive        17.274200
sadness        -15.694206
surprise        -2.115851
trust           -4.557240
dtype: float64

against KPOP

In [271]:
emotion_percentage_kpop = (normalized_mean_emotion_target - normalized_mean_emotion_kpop) / normalized_mean_emotion_kpop * 100

emotion_percentage_kpop

anger           0.0
anticipation    0.0
disgust         0.0
fear            0.0
joy             0.0
negative        0.0
positive        0.0
sadness         0.0
surprise        0.0
trust           0.0
dtype: float64

## Save Data

In [276]:
json_data = {
    "tfidf_counter_global": tfidf_counter_global,
    "tfidf_summer_global": tfidf_summer_global,
    "tfidf_counter_kpop": tfidf_counter_kpop,
    "tfidf_summer_kpop": tfidf_summer_kpop,
    "lda_counter_global": lda_counter_global,
    "lda_summer_global": lda_summer_global,
    "lda_counter_kpop": lda_counter_kpop,
    "lda_summer_kpop": lda_summer_kpop,
    "lda_html_global": lda_html_global,
    "lda_html_kpop": lda_html_kpop,
    "normalized_mean_emotion_target": normalized_mean_emotion_target.astype(float).tolist(),
    "emotion_percentage_global": emotion_percentage_global.astype(float).tolist(),
    "emotion_percentage_kpop": emotion_percentage_kpop.astype(float).tolist(),
}

In [277]:
import json
with open("data_"+ target_group +".json", "w") as f:
    json.dump(json_data, f)

TypeError: Object of type float32 is not JSON serializable